# Modeling Chua's Circuit using a Neural Ordinary Differential Equation

April Herwig

March 2023

In [1]:
using Pkg
Pkg.status()

Project NeuralODEProject v0.1.0
Status `C:\Users\april\Documents\Neural-ODE-Project\Project.toml`
  [fbb218c0] BSON v0.3.7
⌃ [052768ef] CUDA v4.0.1
  [c9c3e87f] ChaoticNDETools v0.2.3 `https://github.com/maximilian-gelbrecht/ChaoticNDETools.jl.git#main`
  [b0b7db55] ComponentArrays v0.13.8
  [aae7a2af] DiffEqFlux v1.54.0
  [0c46a032] DifferentialEquations v7.7.0
  [e30172f5] Documenter v0.27.24
  [587475ba] Flux v0.13.14
  [33d280d1] GAIO v0.3.0 `https://github.com/April-Hannah-Lena/GAIO.jl.git#master`
  [e9467ef8] GLMakie v0.8.3
  [7073ff75] IJulia v1.24.0
  [b2108857] Lux v0.4.45
  [56c15bac] NODEData v0.2.2 `https://github.com/April-Hannah-Lena/NODEData.jl.git#main`
  [7f7a1694] Optimization v3.13.0
  [42dfb2eb] OptimizationOptimisers v0.1.2
  [1dea7af3] OrdinaryDiffEq v6.49.4
  [91a5bcdd] Plots v1.38.8
  [92933f4c] ProgressMeter v1.7.2
  [c35d69d1] SMTPClient v0.6.3
  [1ed8b502] SciMLSensitivity v7.27.0
  [90137ffa] StaticArrays v1.5.19
  [ac1d9e8a] ThreadsX v0.1.11
  [276b4fcb] WG

## Introduction
- why chua's circuit?
- goal: determine amount of data required for satisfying neural ODE

## Research History
- invention of the circuit
- mathematical model
- Lyapunov field

## Machine Learning Model
- neural ODE
- residual neural net -> SkipConnection
- parameter optimization
- stable vs less stable attractors
  
## Discussion
- 

## Introduction

Chua's circuit is a standard case study in the literature on chaotic dynamics [SOURCE]. The simplicity of the mathematical model, a non-stiff three-dimensional system of ordinary differential equations, makes it an attractive example for many numerical experiments. The goal of this project is to train a neural ordinary differential equation using trajectory data, and determine a (heuristic) minimal amount of data required to obtain a satisfying model. 

Chua's circuit was initially developed in 1986 with the goal (among others) to determine whether chaotic dynamics can appear in real-life continuous dynamical systems, or if chaos could only exist in mathematical abstraction [Chua, L.: The genesis of Chua’s circuit. Arch. Elektron.
Übertragungstechnik 42, 250 (1992)]. Indeed, a strange attractor observed in experiment [SOURCE], matching the one observed through numerical simulation. 

A schematic diagram of the simplest canonical Chua's circuit is given in the below figure [Chetvorno, CC0, via Wikimedia Commons]. It consists of four components connected in parallel: two capacitors ($C_1$ and $C_2$) with a resistor $R$ connected between them, as well as an inductor $L$ and a _nonlinear negative resistance_ component $N_R$ called a _Chua diode_ [M.P. Kennedy, "Robust op amp realization of Chua's circuit," in _Proc. First Experimental Chaos Conf._, 1992, pp. 340-351]. 

![Circuit diagram](Chua's_circuit_with_Chua_diode.svg)

Using Kirchoff's laws one derives a set of equations for the three energy storing components. After nondimensionalization the system can be written in a (simplified) canonical form [SOURCE]
$$
\begin{cases}
    \dot{x} &= \alpha \left( y - m_0 x - m_1 f(x) \right) \\
    \dot{y} &= x - y + z \\
    \dot{z} &= - \beta y . 
\end{cases}
$$
where $\alpha, \beta, m_0, m_1$ are real paramters and $f$ is a nonlinear function with fixed point $0$. Note that aside from $f$, the system is entirely linear and hence will not exhibit chaotic behavior. The original Chua oscillator used a piecewise linear function representing the diode's resistance graph, shown below [Chetvorno, CC0, via Wikimedia Commons]. However, many simpler (and smoother) functions still exhibit chaotic dynamics while being more suitable for convergence proofs of numerical algorithms. This project will use a cubic nonlinearity $f(x) = \frac{1}{3} x^3$ with parameters $\alpha = 18,\ \beta = 33,\ m_0 = -0.2,\ m_1 = 0.01$. 

![Voltage-Current Graph](Chua_diode_characteristic_curve.svg)

The Chua oscillator exhibits a strange attractor referred to as the double scroll, as well as a surrounding periodic orbit. These can be initially supposed by observing long trajectories beginning around the two unstable fixed points $x_\pm = \left( \pm \sqrt{-3 m_0 / m_1},\ 0,\ \mp \sqrt{-3 m_0 / m_1} \right)^T$. 

In [2]:
using WGLMakie

In [3]:
# for plotting phase portraits
function chua_axis(; aspect=(1,1.2,1), azimuth=pi/10)
    fig = Figure()
    ax = Axis3(fig[1,1], aspect=aspect, azimuth=azimuth)
    fig, ax
end

chua_axis (generic function with 1 method)

In [4]:
using StaticArrays, OrdinaryDiffEq

In [5]:
# Chua's circuit
function v(u, p, t)
    x, y, z = u
    a, b, m0, m1 = p
    SA{Float32}[ a*(y-m0*x-m1/3.0*x^3), x-y+z, -b*y ]
end

# parameters
p_ode = SA{Float32}[ 18.0, 33.0, -0.2, 0.01 ]
a, b, m0, m1 = p_ode

v(u) = v(u, p_ode, 0f0)

# equilibrium
x₊ = SA{Float32}[ sqrt(-3*m0/m1), 0, -sqrt(-3*m0/m1) ]
x₋ = -x₊

# integration time
t0, t1 = 0f0, 40f0
tspan = (t0, t1)
dt = 1f-2

0.01f0

In [6]:
x0 = SA{Float32}[2, 1.5, 6]
prob = ODEProblem(v, x0, (t0, t1), p_ode)
sol = solve(prob, RK4(), saveat=dt)

retcode: Success
Interpolation: 1st order linear
t: 4001-element Vector{Float32}:
  0.0
  0.01
  0.02
  0.03
  0.04
  0.05
  0.06
  0.07
  0.08
  0.09
  0.1
  0.11
  0.12
  ⋮
 39.89
 39.9
 39.91
 39.92
 39.93
 39.94
 39.95
 39.96
 39.97
 39.98
 39.99
 40.0
u: 4001-element Vector{SVector{3, Float32}}:
 [2.0, 1.5, 6.0]
 [2.3478057, 1.5638899, 5.4943976]
 [2.7161942, 1.625573, 4.9680758]
 [3.1040666, 1.6850694, 4.4217606]
 [3.5098338, 1.7423917, 3.85617]
 [3.931378, 1.7975401, 3.2720225]
 [4.3661227, 1.8505011, 2.6700351]
 [4.8108993, 1.9012377, 2.0509377]
 [5.2620163, 1.9496877, 1.4154711]
 [5.715368, 1.9957609, 0.7644038]
 [6.166409, 2.039319, 0.098552816]
 [6.6104813, 2.0802133, -0.581252]
 [7.042946, 2.1182349, -1.2740747]
 ⋮
 [-9.5907545, -1.1126341, 10.482006]
 [-9.604028, -1.0909499, 10.845691]
 [-9.611745, -1.0660298, 11.201577]
 [-9.614076, -1.0379121, 11.548741]
 [-9.61117, -1.0066366, 11.886193]
 [-9.603076, -0.9723036, 12.212647]
 [-9.5898905, -0.93500376, 12.527375]
 [-9.5717

In [7]:
fig, ax = chua_axis()
scatter!(ax, [x₊, SA[0f0,0f0,0f0], x₋], color=:red, label="Equillibria")
lines!(ax, sol.u, label="Inner Attractor")
Legend(fig[1,2], ax)
fig

In [8]:
x0 = SA{Float32}[2, 1.5, 6]
prob = ODEProblem(v, x0, (t0, t1), p_ode)
sol = solve(prob, RK4(), saveat=dt)

retcode: Success
Interpolation: 1st order linear
t: 4001-element Vector{Float32}:
  0.0
  0.01
  0.02
  0.03
  0.04
  0.05
  0.06
  0.07
  0.08
  0.09
  0.1
  0.11
  0.12
  ⋮
 39.89
 39.9
 39.91
 39.92
 39.93
 39.94
 39.95
 39.96
 39.97
 39.98
 39.99
 40.0
u: 4001-element Vector{SVector{3, Float32}}:
 [2.0, 1.5, 6.0]
 [2.3478057, 1.5638899, 5.4943976]
 [2.7161942, 1.625573, 4.9680758]
 [3.1040666, 1.6850694, 4.4217606]
 [3.5098338, 1.7423917, 3.85617]
 [3.931378, 1.7975401, 3.2720225]
 [4.3661227, 1.8505011, 2.6700351]
 [4.8108993, 1.9012377, 2.0509377]
 [5.2620163, 1.9496877, 1.4154711]
 [5.715368, 1.9957609, 0.7644038]
 [6.166409, 2.039319, 0.098552816]
 [6.6104813, 2.0802133, -0.581252]
 [7.042946, 2.1182349, -1.2740747]
 ⋮
 [-9.5907545, -1.1126341, 10.482006]
 [-9.604028, -1.0909499, 10.845691]
 [-9.611745, -1.0660298, 11.201577]
 [-9.614076, -1.0379121, 11.548741]
 [-9.61117, -1.0066366, 11.886193]
 [-9.603076, -0.9723036, 12.212647]
 [-9.5898905, -0.93500376, 12.527375]
 [-9.5717

In [9]:
fig, ax = chua_axis()
scatter!(ax, [x₊, SA[0f0,0f0,0f0], x₋], color=:red, label="Equillibria")
lines!(ax, sol.u, label="Inner Attractor")

# only slightly different initial condition
x0 = SA{Float32}[2, 1.5, 8]
prob = ODEProblem(v, x0, (t0, t1), p_ode)
sol = solve(prob, RK4(), saveat=dt)

lines!(ax, sol.u, color=:green, label="Outer Attractor")
Legend(fig[1,2], ax)
fig

The existence of the attractor can be numerically proven using a subdivision algorithm from the Julia package GAIO.jl, which provides an outer approximation of the unstable manifolds of $x_\pm$ as well as the chain recurrent set. 

In [10]:
using GAIO

[ Info: GAIO is running on 4 thread(s).


In [11]:
# domain
c, r = (0,0,0), (20,5,20)
Q = GAIO.Box(c, r)

# 120 x 120 x 120 partition of the domain
P = BoxPartition(Q, (120,120,120))
S = cover(P, [x₊, x₋])

# short trajectory (20 steps) to fully cover unstable manifold
f_short(u) = rk4_flow_map(v, u, dt, 20)
F_short = BoxMap(:grid, f_short, Q)

W = unstable_set(F_short, S)

48059 - element BoxSet in 120 x 120 x 120 - element BoxPartition

In [12]:
fig, ax = chua_axis(azimuth=3*pi/10)
plot!(ax, W, color=(:blue, 0.5))
fig

In [13]:
# extend the domain
c, r = (0,0,0), (20,20,120)
Q = GAIO.Box(c, r)

# 1 x  x 1 partition of the domain
P = BoxPartition(Q, (1,1,1))
S = cover(P, :)

# long trajectory to avoid covering "transitional" set
f_long(u) = rk4_flow_map(v, u, dt, 100)
F_long = BoxMap(:grid, f_long, Q)

# 30 subdivision steps to cover the chain recurrent set
C = chain_recurrent_set(F_long, S, steps=24)

# remove the unstable manifold which we already found
P = C.partition
W = cover(P, W)
C = setdiff!(C, W)

7132 - element BoxSet in 256 x 256 x 256 - element BoxPartition

In [14]:
fig, ax = chua_axis(azimuth=pi/5)
plot!(ax, W, color=(:blue, 0.6))
plot!(ax, C, color=(:green, 0.6))
fig

In [15]:
# full interesting set
A = C ∪ W

# short trajectory for computing FTLE field
σ = finite_time_lyapunov_exponents(F_short, A, T=20*dt)

BoxFun in 256 x 256 x 256 - element BoxPartition with 35869 stored weights

In [16]:
fig, ax = chua_axis()
ms = plot!(ax, σ, colormap=(:jet, 0.6))
Colorbar(fig[1,2], ms)
fig

We can conclude that the most chaotic behavior occurs for points lying on the "transition" between to two scrolls of the attractor. We will train two models on long trajectories with different starting values: 
- along the unstable manifold,
- approaching the periodic orbit.
Finally, we will train a model using both datasets. 